# Check Overlapping Events
4.6.2023 a. stein

Something is going wrong with AF/DF computations, here I'm delving into it.

In [1]:
import xarray as xr
import pandas as pd
import numpy as np

from tqdm import tqdm

import sys
sys.path.append('../../')
import ndrought.compare_xy as compare
import ndrought.drought_network_v12 as dnet

import multiprocessing as mp
import os

import pickle
sys.setrecursionlimit(int(1e4))

In [2]:
print('Loading Data')
dm_path = '/pool0/home/steinadi/data/drought/drought_impact/data/drought_measures'

usdm = xr.open_dataset(f'{dm_path}/usdm/USDM_CONUS_105W_20000104_20220412.nc')
print('... USDM loaded')
intervals = ['30d', '180d']
spi = xr.open_dataset(f'{dm_path}/spi/CONUS_105W/spi_usdmcat_CONUS_105W.nc')
print('... SPI loaded')

Loading Data
... USDM loaded
... SPI loaded


In [27]:
spi

<xarray.Dataset>
Dimensions:   (x: 525, y: 702, time: 3066)
Coordinates:
  * x         (x) float64 -2.893e+06 -2.889e+06 ... -6.674e+05 -6.632e+05
  * y         (y) float64 3.251e+06 3.246e+06 3.242e+06 ... 2.717e+05 2.674e+05
  * time      (time) datetime64[ns] 1980-01-05 1980-01-10 ... 2021-12-31
Data variables:
    spi_14d   (time, y, x) float32 ...
    spi_30d   (time, y, x) float32 ...
    spi_90d   (time, y, x) float32 ...
    spi_180d  (time, y, x) float32 ...
    spi_270d  (time, y, x) float32 ...
    spi_1y    (time, y, x) float32 ...
    spi_2y    (time, y, x) float32 ...
    spi_5y    (time, y, x) float32 ...
Attributes:
    units:              USDM Drought Category
    description:        Standardized Precipitation Index
    dimensions:         x y time
    coordinate_system:  EPSG:5070, transformed from EPSG:4326
    Clipping:           This selection has been clipped to everything west of...

In [28]:
usdm_spi_ds = xr.open_dataset('/pool0/home/steinjao/data/drought/drought_impact/data/drought_measures/ndrought_products/CONUS_105W/paired_ds/usdm_spi_paired.nc')

In [30]:
usdm_spi_ds['SPI Date']

<xarray.DataArray 'SPI Date' (index: 1149)>
array(['1999-12-31T00:00:00.000000000', '2000-01-10T00:00:00.000000000',
       '2000-01-15T00:00:00.000000000', ..., '2021-12-21T00:00:00.000000000',
       '2021-12-26T00:00:00.000000000', '2021-12-31T00:00:00.000000000'],
      dtype='datetime64[ns]')
Coordinates:
  * index    (index) int64 0 1 2 3 4 5 6 ... 1142 1143 1144 1145 1146 1147 1148

In [31]:
# pair dates
print ('Pairing Dates ...')
usdm_dates = pd.to_datetime(usdm.time.values)
spi_dates = pd.to_datetime(usdm_spi_ds['SPI Date'].values)

all_dates = [usdm_dates, spi_dates, ]
dm_vars = ['usdm', 'spi', ]
all_dates_dict = {var:dates for var, dates in zip(dm_vars, all_dates)}

usdm_pairings = dict()
for date, var in zip(all_dates, dm_vars):
    if var == 'usdm':
        usdm_pairings[var] = pd.DataFrame(usdm_dates, columns=[var])
    else:
        method = 'last-b'

        usdm_pairings[var] = compare.pair_dates(usdm_dates, date, 'usdm', var, realign=True, method=method)
print('... USDM dates paired')

spi_pairings = dict()
for date, var in zip(all_dates, dm_vars):
    if var == 'spi':
        spi_pairings[var] = pd.DataFrame(spi_dates,  columns=[var])
    else:
        if var == 'grace':
            method = 'last-b'
        else:
            method = 'last-a'
        
        spi_pairings[var] = compare.pair_dates(spi_dates, date, 'spi', var, realign=True, method=method)
print('... SPI dates paired')

Pairing Dates ...
... USDM dates paired
... SPI dates paired


In [32]:
usdm_pairings['spi']

spi                 usdm
0    1999-12-31  2000-01-04 00:00:00
1    2000-01-10  2000-01-11 00:00:00
2    2000-01-15  2000-01-18 00:00:00
3    2000-01-25  2000-01-25 00:00:00
4    2000-01-30  2000-02-01 00:00:00
...         ...                  ...
1144 2021-12-06  2021-12-07 00:00:00
1145 2021-12-11  2021-12-14 00:00:00
1146 2021-12-21  2021-12-21 00:00:00
1147 2021-12-26  2021-12-28 00:00:00
1148 2021-12-31  2022-01-04 00:00:00

[1149 rows x 2 columns]

In [33]:
spi_pairings['usdm']

spi                 usdm
0    1999-12-31  2000-01-04 00:00:00
1    2000-01-10  2000-01-11 00:00:00
2    2000-01-15  2000-01-18 00:00:00
3    2000-01-25  2000-01-25 00:00:00
4    2000-01-30  2000-02-01 00:00:00
...         ...                  ...
1144 2021-12-06  2021-12-07 00:00:00
1145 2021-12-11  2021-12-14 00:00:00
1146 2021-12-21  2021-12-21 00:00:00
1147 2021-12-26  2021-12-28 00:00:00
1148 2021-12-31  2022-01-04 00:00:00

[1149 rows x 2 columns]

In [34]:
all_date_pairings = {
    'usdm':usdm_pairings,
    'spi':spi_pairings,
}

# now to start doing some statistics finally
dm_vars_expanded = {
    'usdm':['USDM'],
    'spi':[f'spi_{interval}' for interval in intervals],
}

dnet_thresholds = {
    'usdm': 2000,
    'spi': 1000,
}

In [35]:
alternate_pairs = []
t = tqdm(total=len(dm_vars)**2, desc='Computing')

all_matched_dates_dicts = []

for var_a in dm_vars:
    for var_b in dm_vars:

        t.set_description(f'Computing {var_a} & {var_b}')

        if not (var_a, var_b) in alternate_pairs:

            in_path = f'{dm_path}/ndrought_products/CONUS_105W/paired_ds/{var_a}_{var_b}_paired.nc'

            paired_ds = xr.open_dataset(in_path)

            var_a_date_idx = []
            for date in all_date_pairings[var_a][var_b][var_a].values:
                var_a_date_idx.append(np.where(all_dates_dict[var_a] == date)[0][0])
            var_b_date_idx = []
            for date in all_date_pairings[var_a][var_b][var_b].values:
                var_b_date_idx.append(np.where(all_dates_dict[var_b] == date)[0][0])
            matched_dates_dict = {var_a_date: var_b_date for var_a_date, var_b_date in zip(var_a_date_idx, var_b_date_idx)}

            all_matched_dates_dicts.append(matched_dates_dict)

            alternate_pairs.append((var_b, var_a))


Computing spi & spi:   0%|          | 0/4 [51:26<?, ?it/s]






In [36]:
alternate_pairs

[('usdm', 'usdm'), ('spi', 'usdm'), ('spi', 'spi')]

In [37]:
len(all_matched_dates_dicts)

3

In [38]:
all_matched_dates_dicts[1]

{0: 0,
 1: 1,
 2: 2,
 3: 3,
 4: 4,
 5: 5,
 6: 6,
 7: 7,
 8: 8,
 9: 9,
 10: 10,
 11: 11,
 12: 12,
 13: 13,
 14: 14,
 15: 15,
 16: 16,
 17: 17,
 18: 18,
 19: 19,
 20: 20,
 21: 21,
 22: 22,
 23: 23,
 24: 24,
 25: 25,
 26: 26,
 27: 27,
 28: 28,
 29: 29,
 30: 30,
 31: 31,
 32: 32,
 33: 33,
 34: 34,
 35: 35,
 36: 36,
 37: 37,
 38: 38,
 39: 39,
 40: 40,
 41: 41,
 42: 42,
 43: 43,
 44: 44,
 45: 45,
 46: 46,
 47: 47,
 48: 48,
 49: 49,
 50: 50,
 51: 51,
 52: 52,
 53: 53,
 54: 54,
 55: 55,
 56: 56,
 57: 57,
 58: 58,
 59: 59,
 60: 60,
 61: 61,
 62: 62,
 63: 63,
 64: 64,
 65: 65,
 66: 66,
 67: 67,
 68: 68,
 69: 69,
 70: 70,
 71: 71,
 72: 72,
 73: 73,
 74: 74,
 75: 75,
 76: 76,
 77: 77,
 78: 78,
 79: 79,
 80: 80,
 81: 81,
 82: 82,
 83: 83,
 84: 84,
 85: 85,
 86: 86,
 87: 87,
 88: 88,
 89: 89,
 90: 90,
 91: 91,
 92: 92,
 93: 93,
 94: 94,
 95: 95,
 96: 96,
 97: 97,
 98: 98,
 99: 99,
 100: 100,
 101: 101,
 102: 102,
 103: 103,
 104: 104,
 105: 105,
 106: 106,
 107: 107,
 108: 108,
 109: 109,
 110: 110,

In [39]:
usdm_spi_dnet = dnet.DroughtNetwork.unpickle('/pool0/home/steinjao/data/drought/drought_impact/data/drought_measures/ndrought_products/CONUS_105W/paired_dnet/USDM_net_spi_match.pickle')

In [40]:
spi_usdm_dnet = dnet.DroughtNetwork.unpickle('/pool0/home/steinjao/data/drought/drought_impact/data/drought_measures/ndrought_products/CONUS_105W/paired_dnet/spi_30d_net_usdm_match.pickle')

In [41]:
overlap_events = usdm_spi_dnet.find_overlapping_nodes_events(spi_usdm_dnet, all_matched_dates_dicts[1])

Overlapping USDM (spi Match) & spi_30d (spi Match):   0%|          | 0/1490319112 [00:00<?, ?it/s]

In [42]:
overlap_events

[[{10: [[time: 10, id: 9, time: 10, id: 1785],
    [time: 10, id: 9, time: 10, id: 1789],
    [time: 10, id: 9, time: 10, id: 1792]]},
  {11: [[time: 11, id: 10, time: 11, id: 2014],
    [time: 11, id: 10, time: 11, id: 2087],
    [time: 11, id: 10, time: 11, id: 2091],
    [time: 11, id: 10, time: 11, id: 2094],
    [time: 11, id: 10, time: 11, id: 2100]]},
  {12: [[time: 12, id: 11, time: 12, id: 2217],
    [time: 12, id: 11, time: 12, id: 2230],
    [time: 12, id: 11, time: 12, id: 2239],
    [time: 12, id: 11, time: 12, id: 2240],
    [time: 12, id: 11, time: 12, id: 2241]]},
  {13: [[time: 13, id: 12, time: 13, id: 2272],
    [time: 13, id: 12, time: 13, id: 2300],
    [time: 13, id: 12, time: 13, id: 2301],
    [time: 13, id: 12, time: 13, id: 2303],
    [time: 13, id: 12, time: 13, id: 2305],
    [time: 13, id: 12, time: 13, id: 2306],
    [time: 13, id: 12, time: 13, id: 2307],
    [time: 13, id: 12, time: 13, id: 2308]]},
  {14: [[time: 14, id: 13, time: 14, id: 2327],
    [ti

Ugh.

Wait a moment, why are the times so high in the matched dates dict?

In [15]:
for node in spi_usdm_dnet:
    print(node.time)

0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4


There are probably no overlaps because those times don't exist!

In [20]:
all_date_pairings['usdm']['spi']['spi']

0      1999-12-31
1      2000-01-10
2      2000-01-15
3      2000-01-25
4      2000-01-30
          ...    
1144   2021-12-06
1145   2021-12-11
1146   2021-12-21
1147   2021-12-26
1148   2021-12-31
Name: spi, Length: 1149, dtype: datetime64[ns]

In [22]:
all_dates_dict['spi']

DatetimeIndex(['1980-01-05', '1980-01-10', '1980-01-15', '1980-01-20',
               '1980-01-25', '1980-01-30', '1980-02-04', '1980-02-09',
               '1980-02-14', '1980-02-19',
               ...
               '2021-11-16', '2021-11-21', '2021-11-26', '2021-12-01',
               '2021-12-06', '2021-12-11', '2021-12-16', '2021-12-21',
               '2021-12-26', '2021-12-31'],
              dtype='datetime64[ns]', length=3066, freq=None)

In [23]:
for date in all_date_pairings['usdm']['spi']['spi']:
    print(np.where(all_dates_dict['spi'] == date)[0][0])

1459
1461
1462
1464
1465
1466
1468
1469
1471
1472
1473
1475
1476
1478
1479
1480
1482
1483
1485
1486
1487
1489
1490
1492
1493
1494
1496
1497
1499
1500
1501
1503
1504
1506
1507
1508
1510
1511
1513
1514
1515
1517
1518
1520
1521
1522
1524
1525
1527
1528
1529
1531
1532
1533
1535
1536
1538
1539
1540
1542
1543
1545
1546
1547
1549
1550
1552
1553
1554
1556
1557
1559
1560
1561
1563
1564
1566
1567
1568
1570
1571
1573
1574
1575
1577
1578
1580
1581
1582
1584
1585
1587
1588
1589
1591
1592
1594
1595
1596
1598
1599
1601
1602
1603
1605
1606
1608
1609
1610
1612
1613
1615
1616
1617
1619
1620
1622
1623
1624
1626
1627
1629
1630
1631
1633
1634
1636
1637
1638
1640
1641
1643
1644
1645
1647
1648
1650
1651
1652
1654
1655
1657
1658
1659
1661
1662
1664
1665
1666
1668
1669
1671
1672
1673
1675
1676
1678
1679
1680
1682
1683
1685
1686
1687
1689
1690
1692
1693
1694
1696
1697
1699
1700
1701
1703
1704
1706
1707
1708
1710
1711
1713
1714
1715
1717
1718
1720
1721
1722
1724
1725
1727
1728
1729
1731
1732
1734
1735
1736
1738


Ohhhhhhhhhh, right. The SPI dates back to 1980, but the network was built from the 2000's onward.

In [26]:
spi_usdm_dnet.data.shape

(1149, 702, 525)